In [1]:
# imports
import pandas as pd
import numpy as np
from ipyleaflet import (Map, GeoData, basemaps, WidgetControl, GeoJSON,
 LayersControl, Icon, Marker,basemap_to_tiles, Choropleth,
 MarkerCluster, Heatmap,SearchControl, 
 FullScreenControl)
from ipywidgets import Text, HTML
from branca.colormap import linear
import geopandas as gpd
import json

In [2]:
# files
file1 = 'data/driver_rides.csv'
file2 = 'data/driver_sessions.csv'

In [3]:
# initial file dataframes
driver_rides_df = pd.read_csv(file1)
driver_sessions_df = pd.read_csv(file2)

### Create DataFrame of When and Where Rides are Accepted

In [5]:
# pull file
driver_rides_df

status       accepted_timestamp  accepted_lat  accepted_lng  \
0     finished  2021-07-08 20:57:56 UTC     29.436080    -98.494540   
1     finished  2021-07-08 06:41:29 UTC     29.424580    -98.500380   
2     canceled  2021-07-08 01:49:01 UTC     29.487599    -98.608716   
3     finished  2021-07-08 22:39:27 UTC     29.467350    -98.491890   
4     finished  2021-07-08 05:28:51 UTC     29.527446    -98.477111   
...        ...                      ...           ...           ...   
1112  finished  2021-10-05 21:49:34 UTC     29.592361    -98.582359   
1113  finished  2021-11-10 01:11:44 UTC     29.426483    -98.488251   
1114  finished  2021-10-25 23:25:34 UTC     29.539421    -98.571307   
1115  finished  2021-10-25 18:00:17 UTC     29.417805    -98.683061   
1116  finished  2021-10-25 19:46:39 UTC     29.488210    -98.501600   

             pickup_timestamp  pickup_lat  pickup_lng  \
0     2021-07-08 21:01:30 UTC         NaN         NaN   
1     2021-07-08 06:45:36 UTC         NaN         NaN   
2                         NaN         NaN         NaN   
3     2021-07-08 22:42:04 UTC         NaN         NaN   
4     2021-07-08 05:46:57 UTC         NaN         NaN   
...                       ...         ...         ...   
1112  2021-10-05 22:09:52 UTC         NaN         NaN   
1113  2021-11-10 01:17:10 UTC         NaN         NaN   
1114  2021-10-25 23:35:26 UTC         NaN         NaN   
1115  2021-10-25 18:05:44 UTC         NaN         NaN   
1116  2021-10-25 19:52:14 UTC         NaN         NaN   

        dropped_off_timestamp  dropoff_lat  dropoff_lng  
0     2021-07-08 21:15:05 UTC          NaN          NaN  
1     2021-07-08 07:08:28 UTC          NaN          NaN  
2                         NaN          NaN          NaN  
3     2021-07-08 22:56:26 UTC          NaN          NaN  
4     2021-07-08 06:03:00 UTC          NaN          NaN  
...                       ...          ...          ...  
1112  2021-10-05 22:31:45 UTC          NaN          NaN  
1113  2021-11-10 01:24:43 UTC          NaN          NaN  
1114  2021-10-25 23:45:53 UTC          NaN          NaN  
1115  2021-10-25 18:25:29 UTC          NaN          NaN  
1116  2021-10-25 20:02:02 UTC          NaN          NaN  

[1117 rows x 10 columns]

In [11]:
# drop unneccesary columns, drop columns with NaN
# this data shows length of time in the lifecycle of each ride
# the lifecycle is - accept ride, pickup rider, dropoff rider

driver_timestamps_df = driver_rides_df.drop(['status','pickup_lat','pickup_lng','dropoff_lat','dropoff_lng'], axis = 1)
driver_timestamps_df

accepted_timestamp  accepted_lat  accepted_lng  \
0     2021-07-08 20:57:56 UTC     29.436080    -98.494540   
1     2021-07-08 06:41:29 UTC     29.424580    -98.500380   
2     2021-07-08 01:49:01 UTC     29.487599    -98.608716   
3     2021-07-08 22:39:27 UTC     29.467350    -98.491890   
4     2021-07-08 05:28:51 UTC     29.527446    -98.477111   
...                       ...           ...           ...   
1112  2021-10-05 21:49:34 UTC     29.592361    -98.582359   
1113  2021-11-10 01:11:44 UTC     29.426483    -98.488251   
1114  2021-10-25 23:25:34 UTC     29.539421    -98.571307   
1115  2021-10-25 18:00:17 UTC     29.417805    -98.683061   
1116  2021-10-25 19:46:39 UTC     29.488210    -98.501600   

             pickup_timestamp    dropped_off_timestamp  
0     2021-07-08 21:01:30 UTC  2021-07-08 21:15:05 UTC  
1     2021-07-08 06:45:36 UTC  2021-07-08 07:08:28 UTC  
2                         NaN                      NaN  
3     2021-07-08 22:42:04 UTC  2021-07-08 22:56:26 UTC  
4     2021-07-08 05:46:57 UTC  2021-07-08 06:03:00 UTC  
...                       ...                      ...  
1112  2021-10-05 22:09:52 UTC  2021-10-05 22:31:45 UTC  
1113  2021-11-10 01:17:10 UTC  2021-11-10 01:24:43 UTC  
1114  2021-10-25 23:35:26 UTC  2021-10-25 23:45:53 UTC  
1115  2021-10-25 18:05:44 UTC  2021-10-25 18:25:29 UTC  
1116  2021-10-25 19:52:14 UTC  2021-10-25 20:02:02 UTC  

[1117 rows x 5 columns]

In [6]:
# output to csv for tableau
#driver_timestamps_df.to_csv("output/driver_timestamps_df.csv")

### Create DataFrame of Driver Start and End

In [7]:
# this data shows start of driving sessions, the duration of the session in hours
# the start and end location of each session
driver_sessions_df

start_time  duration  start_lat  start_lng    end_lat  \
0    2021-09-14 20:06:57 UTC  2.067222  29.435288 -98.689173  29.536882   
1    2021-08-25 21:46:35 UTC  3.051111  29.589127 -98.622194  29.402338   
2    2021-08-25 21:06:04 UTC  0.080556  29.531697 -98.496517  29.512041   
3    2021-08-25 21:00:53 UTC  0.083889  29.537560 -98.490436  29.531704   
4    2021-08-25 19:25:50 UTC  1.166389  29.428396 -98.524946  29.443699   
..                       ...       ...        ...        ...        ...   
314  2021-11-09 22:17:56 UTC  1.187778  29.439506 -98.674204  29.486114   
315  2021-11-09 04:33:27 UTC  0.058611  29.480490 -98.711058  29.471683   
316  2021-11-09 03:50:37 UTC  0.710833  29.520658 -98.602415  29.482744   
317  2021-11-09 03:26:07 UTC  0.342778  29.519226 -98.612390  29.519993   
318  2021-11-09 02:46:01 UTC  0.555833  29.526669 -98.600435  29.519652   

       end_lng  
0   -98.522610  
1   -98.510157  
2   -98.534580  
3   -98.496514  
4   -98.477564  
..         ...  
314 -98.453389  
315 -98.696407  
316 -98.711356  
317 -98.602834  
318 -98.611638  

[319 rows x 6 columns]

In [8]:
# output to csv file for tableau
#driver_start_end_df.to_csv("output/driver_start_end_df.csv")

### GeoMap Passenger Requests with GeoPandas

In [9]:
texas_shape = gpd.read_file('shape/State.shp')
texas_shape.iloc[0]['geometry']

In [10]:
str(texas_shape.iloc[0]['geometry'])

'POLYGON ((-100.5002487199999 36.49986621100004, -100.494608719 36.49988621100005, -100.487938718 36.49992621000007, -100.430688698 36.49989621900005, -100.406658692 36.49989621500004, -100.368898681 36.49988622300003, -100.3223286749999 36.49986622100005, -100.3025586699999 36.49986622200004, -100.292678665 36.49985622200006, -100.282678668 36.49987622000003, -100.2775786609999 36.49987622400005, -100.267368655 36.49988622400008, -100.250578655 36.49989622500004, -100.249848657 36.49986622300003, -100.2381986509999 36.49985623000003, -100.2323786489999 36.49985622700007, -100.2244986489999 36.49986622700004, -100.2181686489999 36.49986622800003, -100.2126386469999 36.49987622400005, -100.180598638 36.49985623300006, -100.1638386339999 36.49987623400006, -100.158968633 36.49987622900005, -100.1214386189999 36.49982623400007, -100.102788618 36.49987623400006, -100.097808621 36.49985622900005, -100.0892486129999 36.49984623300003, -100.08094861 36.49985623500004, -100.0701886149999 36.49